<a href="https://colab.research.google.com/github/Borja21091/Autonomous-Flight-Module-ROS/blob/main/BTC_charts.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Install libraries

In [127]:
# Erases all variables
%reset -f
!pip install colour
!pip install --upgrade --no-cache-dir git+https://github.com/borja21091/tvdatafeed.git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/borja21091/tvdatafeed.git to /tmp/pip-req-build-0at389so
  Running command git clone --filter=blob:none --quiet https://github.com/borja21091/tvdatafeed.git /tmp/pip-req-build-0at389so
  Resolved https://github.com/borja21091/tvdatafeed.git to commit e6f6aaa7de439ac6e454d9b26d2760ded8dc4923
  Preparing metadata (setup.py) ... done


# Import necessary libraries

In [128]:
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd
import scipy.stats as stats
import scipy.optimize as opt
import scipy.signal as sig
import numpy as np
import calendar
import numbers
import plotly.figure_factory as ff
from tvDatafeed import TvDatafeed, Interval
from more_itertools import pairwise
from scipy.signal.waveforms import nan
from pandas.io.parsers.readers import RangeIndex
from pandas.core.frame import to_arrays
from plotly.subplots import make_subplots
from colour import Color
from ipywidgets import widgets,HBox,VBox,interactive_output,Layout
from scipy.stats import nct

<ipython-input-128-de6cde6db661>:14: DeprecationWarning:

Please use `nan` from the `scipy.signal` namespace, the `scipy.signal.waveforms` namespace is deprecated.



# Get Data from TradingView

In [129]:
tv = TvDatafeed()
crypto = tv.get_hist(symbol='BTCUSD',exchange='INDEX',interval=Interval.in_daily,n_bars=5000)
crypto['Date'] = crypto.index
crypto.index = range(crypto.shape[0])
crypto['idx'] = crypto.index

# Supporting Functions

## Regression

In [130]:
def regCurve(x, a, b, c):
  out = a * np.log10(b + x) + c
  return out

def fitCurve(cryptodf, X, logY):
  popt, pcov = opt.curve_fit(regCurve, X, logY)
  # Confidence interval of fit
  sigma = np.sqrt(np.diagonal(pcov))
  logCurve = regCurve(cryptodf.idx, *popt)
  upper = 10**(regCurve(cryptodf.idx, *(popt + sigma)))
  lower = 10**(regCurve(cryptodf.idx, *(popt - sigma)))
  curve = 10**(logCurve)
  return curve, logCurve, upper, lower, popt

def cycleDates(cryptodf):
  price = cryptodf.close
  # Peaks idx and Dates
  pidx, _ = sig.find_peaks(x=price, distance=850)
  pDates = cryptodf.Date[np.append(pidx,(cryptodf.tail(1).index.item()))]
  vidx = []
  for x, y in pairwise(pDates):
    idx = pd.Series.idxmin(cryptodf.close[(cryptodf.Date > x) & (cryptodf.Date < y)])
    vidx.append(idx)
  vDates = cryptodf.Date[vidx]
  
  return pDates[0:-1:1],vDates

def linearEq(x,a,b,c):
  return a*(x+b) + c

def filterOutliers(filter,cryptodf,threshold):
  # Initialization
  MSE = 1000
  curveOld = 0
  iteration = 0

  while MSE > 10**(-7):
    # Filter data to be fitted
    X = cryptodf.idx[filter]
    Y = np.log10(cryptodf.close[filter])
    # Fit curve
    curve, logCurve, upper, lower, params = fitCurve(crypto, X, Y)
    # Error
    MSE = ((curveOld - logCurve)**2).mean()
    curveOld = logCurve
    # Extension of price from curve (zScore)
    tmp = np.log10(10**(Y) / curve[filter])
    # stdev = np.sqrt(np.matmul(tmp,tmp) / tmp.shape[0])
    stdev = np.sqrt(np.cumsum(np.square(tmp)) / np.arange(1,tmp.shape[0] + 1))
    zScore = tmp / stdev
    # Find outliers (zScore < -2 + zScore > 2)
    outlier = zScore.index[(zScore > threshold[1]) | (zScore < threshold[0])].tolist()
    filter[outlier] = False
    
    # Add iteration counter
    iteration += 1
    if iteration > 50:
      return curve, upper, lower

  return curve, upper, lower


## ROI

In [131]:
def calc_roi(window, label):
  roi = crypto['close'] / crypto['close'].shift(window)
  # Generate dict
  out = {'x' : [crypto['Date']],
         'y' : [roi, crypto['close']],
         'name' : ['ROI %s' % label, 'price']}
  
  return out

def gen_roi_buttons(labels, windows):
  # Loop and generate button dicts
  out = list()
  for L,W in zip(labels,windows):
    out.append(dict(
        label = L,
        method = 'update',
        args = [calc_roi(W, L)]
    ))
  return out

## Momentum

In [132]:
def momentum(df,time_unit):
  out = np.zeros([df.shape[0],len(time_unit)])
  detrend = np.log10(df['close'] / df['Fair']) # df['close'].rolling(df.shape[0], min_periods=1).mean())
  for idx, t in enumerate(time_unit):
    tmp = detrend - detrend.shift(t)
    out[:,idx] = (tmp - tmp.rolling(len(tmp),min_periods=1).mean()) / tmp.rolling(len(tmp),min_periods=1).std()
    # out[:,idx] = tmp
    # out[:,idx] = np.log10(df['close'] / df['close'].shift(t))
  return out, detrend

def normalise(data):
  return (data - data.min()) / (data.max() - data.min())

def derivative(data):
  # out = (data - data.shift(order)) / order
  out = (5*data + 2*data.shift() - 8*data.shift(2) - 2*data.shift(3) + 3*data.shift(4)) / 8 # http://www.holoborodko.com/pavel/numerical-methods/numerical-derivative/smooth-low-noise-differentiators/

  return out

## Volatility

In [133]:
def sample_closest_values(x,alpha):
    median = np.median(x)
    distances = np.abs(x - median)
    sorted_indices = np.argsort(distances)
    closest_indices = sorted_indices[:int(len(x) * (1-alpha))]
    closest_values = x[closest_indices]
    return closest_values

def dist_window(data,window):
  samples = []
  for W in window:
    r = data.tail(int(W))
    # Fit Distribution to data
    param = nct.fit(r)
    x = nct.rvs(*param,size=1000)
    samples.append(sample_closest_values(x,0.05))
  return samples

# Fit Fair, Non-bubble & Bubble data

In [134]:
# Dates of cycles (Peaks & Valleys)
pDates, vDates = cycleDates(crypto)

# Date Filter --> Current Cycle low / Last cycle low --> iloc[-2]
dateFilter = vDates.iloc[-2]

# Fair Value up to last cycle low
xData = crypto.idx[crypto['Date'] < dateFilter]
yData = np.log10(crypto.close[crypto['Date'] < dateFilter])

fairValue, _, fairUpper, fairLower, params = fitCurve(crypto, xData, yData) # Fit to all data until certain date
# fairValue, _, fairUpper, fairLower = fitCurve(crypto, crypto.idx, np.log10(crypto.close)) # Fit to all data
crypto['Fair'] = fairValue.tolist()
crypto['Fair_Up'] = fairUpper.tolist()
crypto['Fair_Low'] = fairLower.tolist()

# Data below Fair Value & up to last cycle low
filter = (crypto['close'] < crypto['Fair']) & (crypto['Date'] < dateFilter)
filter_bfv = [i for i in filter] # Don't do --> filter_bfv = filter --> both point to the same object 
# Fit curve filtering outliers
nbValue,nbUpper, nbLower = filterOutliers(filter, crypto, [-2,2])
crypto['NB'] = nbValue.tolist()
crypto['NB_Up'] = nbUpper.tolist()
crypto['NB_Low'] = nbLower.tolist()

# Fit Peak Data from past cycles
try:
  bValue, _, bUpper, bLower = fitCurve(crypto, crypto.idx[pDates.index[0:-1]], np.log10(crypto.close[pDates.index[0:-1]]))
  crypto['B'] = bValue.tolist()
  crypto['B_Up'] = bUpper.tolist()
  crypto['B_Low'] = bLower.tolist()
except:
  print('Error with Bubble Data')
  crypto['B'] = nan
  crypto['B_Up'] = nan
  crypto['B_Low'] = nan


Error with Bubble Data


/usr/local/lib/python3.10/dist-packages/scipy/optimize/_minpack_py.py:906: OptimizeWarning:

Covariance of the parameters could not be estimated

/usr/local/lib/python3.10/dist-packages/pandas/core/arraylike.py:402: RuntimeWarning:

invalid value encountered in log10



# Plot Data

## Regression Curves

In [135]:
fig = px.line(crypto, x='Date', y=['close','B','Fair','NB'],
              log_y=True, template='plotly_dark',
              color_discrete_sequence=['rgb(255,255,255)', 'rgb(255,0,0)', 'rgb(212,184,85)', 'rgb(72,179,54)'])
fig.update_layout(yaxis_title="Price ($)")

# Confidence levels
fig.add_trace(go.Scatter(
    x=crypto['Date'].tolist() + crypto['Date'].iloc[::-1].tolist(),
    y=crypto['B_Up'].tolist() + crypto['B_Low'].iloc[::-1].tolist(),
    fill='toself',
    fillcolor='rgba(255,0,0,0.2)',
    line_color='rgba(255,0,0,0)',
    name='B Confidence',
    visible='legendonly',
    hoveron='points',
    showlegend=True))
fig.add_trace(go.Scatter(
    x=crypto['Date'].tolist() + crypto['Date'].iloc[::-1].tolist(),
    y=crypto['Fair_Up'].tolist() + crypto['Fair_Low'].iloc[::-1].tolist(),
    fill='toself',
    fillcolor='rgba(212,184,85,0.2)',
    line_color='rgba(212,184,85,0)',
    name='Fair Confidence',
    visible='legendonly',
    hoveron='points',
    showlegend=True))
fig.add_trace(go.Scatter(
    x=crypto['Date'].tolist() + crypto['Date'].iloc[::-1].tolist(),
    y=crypto['NB_Up'].tolist() + crypto['NB_Low'].iloc[::-1].tolist(),
    fill='toself',
    fillcolor='rgba(72,179,54,0.2)',
    line_color='rgba(72,179,54,0)',
    name='NB Confidence',
    visible='legendonly',
    hoveron='points',
    showlegend=True))

# Show datapoints used to fir Non-bubble regression curve
fig.add_trace(go.Scatter(
    x=crypto.Date[filter],
    y=crypto.close[filter],
    name='NB Fitting Data',
    mode='markers',
    marker=dict(color='purple',size=10)))

fig.update_layout(height=800)

fig.show()

## Percentage Extension from Fair Value

In [136]:
crypto['Ext_Fair'] = crypto['close']*100 / crypto['Fair']

fig = px.line(crypto, x='Date', y='Ext_Fair',
              labels={'Ext_Fair' : 'Extension from Fair Value (%)',
                      'Date' : ''},
              color_discrete_sequence = ['rgb(255,255,255)'],
              log_y=True, template='plotly_dark')

fig.add_shape(type='line', x0=crypto.Date.iloc[0], y0=100, x1=crypto.Date.iloc[-1], y1=100,
                line=dict(color='Red',), secondary_y=False)
fig.show()

## ROI

### Running ROI

In [137]:
# Dropdown Parameters
roi_window = [30, 90, 180, 365, 2*365, 3*365, 4*365]
roi_labels = ['30D', '90D', '180D', '1Y', '2Y', '3Y', '4Y']

# Create Figure
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.update_yaxes(type='log')
fig.update_layout(template='plotly_dark', height=800, legend=dict(orientation='h'))
fig.update_yaxes(title_text='ROI', secondary_y=False, showgrid=True)
fig.update_yaxes(title_text='Price(USD)', secondary_y=True, showgrid=False)
# Trace for ROI
fig.add_trace(go.Scatter(
    marker = dict(color='orange'),
    showlegend=True),
    secondary_y = False
)
# Trace for Asset price
fig.add_trace(go.Scatter(
    marker = dict(color='white'),
    showlegend=True),
    secondary_y = True
)

# Add dropdowns
fig.update_layout(
    updatemenus=[go.layout.Updatemenu(
        buttons=list(gen_roi_buttons(roi_labels, roi_window)),
            x=0.04,
            xanchor="left",
            y=1.15,
            yanchor="top"
        )
    ])

# Add annotation to dropdown menu
fig.update_layout(
    annotations=[
        dict(text='Window', x=0, xref="paper", y=1.13, yref="paper",
                             align="left", showarrow=False)
    ])

fig.show()

### Monthly Returns (%)

In [138]:
# Group by Years
years = crypto.groupby(crypto['Date'].dt.year)
# Group by Months
m_keys = ['Year','January','February','March','April','May','June','July','August',
          'September','October','November','December']
months = crypto.groupby(crypto['Date'].dt.month)
# Monthly Returns
m_returns = pd.DataFrame(index=years.groups.keys(), columns=m_keys)
for idx,Y in enumerate(years.groups.keys()):
  y_idx = years.groups.get(Y)
  months = crypto.groupby(crypto['Date'][y_idx].dt.month)
  m_returns['Year'][Y] = Y
  for M in months.groups.keys():
    name = m_keys[(int(M) % len(m_keys))]
    m_idx = months.groups.get(M)
    m_returns[name][Y] = round(100 * (crypto['close'][m_idx[-1]] - crypto['open'][m_idx[0]]) / crypto['open'][m_idx[0]],2)
# Flip Monthly Returns --> First row is current year >> Last row is start year of the asset
m_returns = m_returns[::-1]
# Cell colors
fill_color=m_returns.apply(lambda s: np.where(s.values > 0,'rgb(99, 179, 89)',np.where(s.values < 0,'rgb(222, 95, 95)','grey')) ,).T.values
fill_color[0] = ['darkgrey']*len(years.groups.keys()) # Color for 'Year' column
# Create Figure
fig = make_subplots(rows=2,cols=1,specs=[[{"type": "table"}],[{"type": "table"}]],
                    vertical_spacing=0.01,row_heights=[0.85,0.15])
# Add Monthly return Table figure
fig.add_trace(
    go.Table(
        header=dict(values=m_keys,align='center'),
        cells=dict(values=m_returns.transpose(),
                   fill_color=fill_color,height=30)
    ),
    row=1,
    col=1
)
# Average and std Table
mu = m_returns.mean()[1:None].round(2)
sigma = m_returns.std()[1:None].round(2)
tmp = ['%s \u00B1 %s' % (mean,stdev) for mean,stdev in zip(mu,sigma)]
tmp.insert(0,'Avg \u00B1 Std')
tmp_color = ['darkgrey'] + np.where(mu > 0,'rgb(99, 179, 89)','rgb(222, 95, 95)').tolist()

fig.add_trace(
    go.Table(
        header=dict(fill_color='rgba(0,0,0,0)'),
        cells=dict(values=tmp,fill_color=tmp_color,height=30)
    ),
    row=2,
    col=1
)

fig.update_layout(template='plotly_dark',height=700,margin=dict(t=50,b=50))
fig.show()

<ipython-input-138-78283060f84f>:20: RuntimeWarning:

invalid value encountered in greater

<ipython-input-138-78283060f84f>:20: RuntimeWarning:

invalid value encountered in less



### Year-to-Date ROI

In [139]:
# Group by Years
years = crypto.groupby(crypto['Date'].dt.year)

# Plot Data
fig = go.Figure()#layout_yaxis_range=[0,1])
fig.update_yaxes(type='log')
fig.update_layout(template='plotly_dark', showlegend=True, height=800, legend=dict(orientation='h'))
fig.update_yaxes(title_text='Y-t-D ROI')
fig.update_xaxes(title_text='Days')

ytd_roi = pd.Series('float64')
for j in years.groups.keys():
  idx = np.array(years.groups.get(j))
  roi = crypto['close'][idx] / crypto['close'][idx[0]]
  pd.concat([ytd_roi,roi])
  days = idx - idx[0] + 1
  title = "%s" % j
  fig.add_trace(
      go.Scatter(x=days, y=roi, name=title))
fig.show()
crypto['Y-t-D ROI'] = ytd_roi

### Drawdown ROI since Cycle-Top

In [140]:
# Drawdown ROI
crypto['Drawdown_ROI'] = crypto['close'] / crypto['close'].cummax()

# Plot Data
fig = go.Figure()#layout_yaxis_range=[0,1])
fig.update_yaxes(type='log')
fig.update_layout(template='plotly_dark', showlegend=True, height=800, legend=dict(orientation='h'))
fig.update_yaxes(title_text='ROI')
fig.update_xaxes(title_text='Days since Peak')

for j in np.arange(len(pDates)):
  idx = np.arange(pDates.index[j],vDates.index[j]+1,1)
  title = "Cycle %s" % (j+1)
  fig.add_trace(
      go.Scatter(x=np.arange(1,len(idx)+1,1), y=crypto.Drawdown_ROI[idx],
                 name=title))
fig.show()

### ROI Bands

In [141]:
# Create Figure
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.update_yaxes(type='log')
fig.update_layout(template='plotly_dark', height=800, legend=dict(orientation='h'))
fig.update_yaxes(title_text='ROI Days', secondary_y=False, showgrid=True)
fig.update_yaxes(title_text='Price(USD)', secondary_y=True, showgrid=False)

price = crypto['close'].to_numpy()
n = len(price)
# Divide each price by all prices (Symmetric matrix) & zero upper triangle
roi_mat = np.tril(np.outer(price,1/price)) # column i --> all values / price[i]
roi_mat[roi_mat == 0] = np.nan # Replace '0' --> 'nan' to avoid problems filtering
roi_band_bullish = [2, 5, 10, 25, 50, 100]
roi_band_bearish = [0.5, 0.2, 0.1]
roi_band = roi_band_bullish + roi_band_bearish
# Band colors
roi_color_bullish = list(Color('red').range_to(Color('green'),len(roi_band_bullish)))
roi_color_bearish = list(Color('blue').range_to(Color('gray'),len(roi_band_bearish)))
roi_color = roi_color_bullish + roi_color_bearish

for index, item in enumerate(roi_band):
  roiBandName = 'Days to x%s' % item
  if roiBandName not in crypto:
    if index <= len(roi_color_bullish) - 1:
      idx = np.argmax(roi_mat>=item, axis=0) # First occurence of roi >= bullish roi multiplier
    else: 
      idx = np.argmax(roi_mat<=item, axis=0) # First occurence of roi <= bearish roi_band multiplier
    idx = idx.astype('float')
    idx[idx == 0] = np.nan # Replace '0' for 'nan' for plotting
    idx -= (np.arange(n) + 1) # Calculate number of days
    crypto[roiBandName] = idx # Update dataframe

  fig.add_trace(go.Scatter(
    x = crypto['Date'],
    y = crypto[roiBandName],
    name = 'x%s' % item,
    mode = 'markers',
    marker = dict(color = roi_color[index].hex,
                  opacity = 0.5)
  ))

# Add Price of Asset
fig.add_trace(go.Scatter(
    x = crypto['Date'],
    y = crypto['close'],
    marker = dict(color='white'),
    name = 'price'),
    secondary_y = True
)

# Add dropdown menus (Bullish/Bearish/Both)
fig.update_layout(
    updatemenus=[go.layout.Updatemenu(
        active=2,
        buttons=list(
            [dict(label = 'Bullish',
                  method = 'update',
                  args = [{'visible': [True]*len(roi_band_bullish) + [False]*len(roi_band_bearish) + [True]},
                          {'showlegend':True}]),
             dict(label = 'Bearish',
                  method = 'update',
                  args = [{'visible': [False]*len(roi_band_bullish) + [True]*len(roi_band_bearish) + [True]},
                          {'showlegend':True}]),
             dict(label = 'Both',
                  method = 'update',
                  args = [{'visible': [True]*(len(roi_band) + 1)},
                          {'showlegend':True}]),
            ]),
            x=0.06,
            xanchor="left",
            y=1.15,
            yanchor="top"
        )
    ])

# Add annotation to dropdown menu
fig.update_layout(
    annotations=[
        dict(text='Multiplier Bias', x=0, xref="paper", y=1.14, yref="paper",
                             align="left", showarrow=False)
    ])

fig.show()

## Momentum

### Dual Momentum Oscillator

In [142]:
# Calculate Momentums
t_unit = np.array([7,14,30])
m, detrend = momentum(crypto,t_unit)

# Weight momentums to calculate 'Total_Momentum'
weights = np.reciprocal(t_unit.astype('float'))
weights = weights / np.sum(weights) # Make sure sum of weights == 1
# weights = np.array([0.47, 0.33, 0.2])

# Calculate Weighted Momentum
w_m = pd.Series(np.sum(np.multiply(weights, m), axis=1))
# F = (params[1] + crypto.index)*np.log(10)/params[0] # 1/regression_curve_derivative
# w_m = w_m*F
# dw_m = derivative(w_m)
w_m = w_m.rolling(40, min_periods=1).mean() # 2*normalise(w_m.rolling(40).mean()) - 1
window = len(w_m)
crypto['W_Momentum'] = w_m # (w_m - w_m.rolling(window, min_periods=1).mean()) / w_m.rolling(window, min_periods=1).std()

# Create figure
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.update_yaxes(type='linear', secondary_y=True)
fig.update_yaxes(type='log', secondary_y=False)
fig.update_layout(template='plotly_dark', showlegend=True, height=800, legend=dict(orientation='h'))
fig.update_yaxes(title_text='Price (USD)', secondary_y=False, showgrid=True)
fig.update_yaxes(title_text='Momentum', secondary_y=True, showgrid=False)
# Add Price colored based on Momentum
fig.add_trace(go.Scatter(
                x=crypto['Date'], y=crypto['close'],
                name='price',
                marker=dict(color='white')))
# Add W_Momentum on secondary Y Axis
fig.add_trace(go.Scatter(
                x=crypto['Date'], y=crypto['W_Momentum'],
                mode='markers',
                marker=dict(color=crypto['W_Momentum'],
                            colorscale='Portland',
                            size=3),
                name='Momentum'),
              secondary_y = True)


### Momentum-Flip Price

In [143]:
# Delay Units used for Momentum
t_unit = np.array([7,14,30])
# Weights assigned to each Momentum component
weights = np.array([0.47, 0.33, 0.2])

# Price that makes momentum flip bullish or bearish
m_neutral = 1.0
shifted = np.array([crypto['close'].shift(t) for t in t_unit]).transpose()
p = m_neutral / (np.divide(weights, shifted).sum(axis=1))
p = pd.Series(p).rolling(40,min_periods=1).mean()

# Create figure
fig = go.Figure()
fig.update_yaxes(type='log')
fig.update_layout(template='plotly_dark', showlegend=True, height=800, legend=dict(orientation='h'))
fig.update_yaxes(title_text='Price (USD)')
# Add Price colored based on Momentum
fig.add_trace(go.Scatter(
                x=crypto['Date'], y=crypto['close'],
                name='price',
                marker=dict(color='white')))
# Add Momentum-Flip Price
fig.add_trace(go.Scatter(
                x=crypto['Date'], y=p,
                name='Threshold',
                mode='markers',
                marker=dict(size=3,
                            color=(p > crypto['close']).astype('int'),
                            colorscale=[[0, 'green'], [1, 'red']])))

## Volatility

### Z-Score

In [144]:
# Z-Score Parameters
zscore_window = [7, 30, 90, 365, 4*365]
zscore_labels = ['D7', 'D30', 'D90', 'Y1', 'Y4']

# Sliders
sliders = []
for L in zscore_labels:
  w = widgets.FloatSlider(
      value=1,
      min=0,
      max=1,
      step=0.1,
      description=L,
      disabled=False,
      continuous_update=False,
      orientation='vertical',
      layout=Layout(height='150px'),
      readout=False,
      readout_format='.1f')
  sliders.append(w)
box = HBox(sliders)

# Calculate Z-Scores
zscore = pd.DataFrame()
for w in zscore_window:
  MA = crypto['close'].rolling(w,min_periods=1).mean()
  stdev = crypto['close'].rolling(w,min_periods=1).std()
  zscore[w] = (crypto['close'] - MA) / stdev

# Create figure
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.update_yaxes(type='linear', secondary_y=True)
fig.update_yaxes(type='log', secondary_y=False)
fig.update_layout(template='plotly_dark', showlegend=False)
fig.update_yaxes(title_text='Price (USD)', secondary_y=False, showgrid=True)
fig.update_yaxes(title_text='Z-Score', secondary_y=True, showgrid=False)
# Add Price
fig.add_trace(go.Scatter(
                x=crypto['Date'], y=crypto['close'],
                name='price',
                marker=dict(color='white')))
# Add Z-Score
fig.add_trace(go.Scatter(
                x=crypto['Date'],
                name='Z-Score'),
              secondary_y = True)

# Interactive Sliders
def calc_zscore(D7, D30, D90, Y1, Y4):
  weights = np.array([x for x in list(locals().values())])
  tmp = zscore.dot(weights/np.sum(weights))
  crypto['Z-Score'] = tmp
  # Update Trace
  fig.data[1].y = tmp
  f2 = go.FigureWidget(fig)
  f2.update_layout(height=800, width=1750)
  f2.show()

out = interactive_output(calc_zscore,{L : W for W,L in zip(box.children,zscore_labels)})
display(VBox([box,out]))

### Return Z-Score based Forecasting

In [145]:
# 1. Log10 returns Z-Score
window=1
ret = np.log10(crypto['close']/crypto['close'].shift(window))
std_returns = ret.rolling(ret.size,min_periods=1).std()
CMA_returns = ret.rolling(ret.size,min_periods=1).mean()
crypto['ret'] = (ret - CMA_returns) / std_returns

# 2. Distribution of log returns Z-Score
dWindow = np.array([7,14,30,2*30,3*30,4*30,6*30,8*30,10*30,365])/window
dLabels = ['1W','2W','1M','2M','3M','4M','6M','8M','10M','1Y']
s = dist_window(crypto['ret'],dWindow)

# 3. Transform log returns Z-Score >> Price
logP = np.array(s)*std_returns.iloc[-2] + CMA_returns.iloc[-2]
pForecast = 10**(logP) * crypto['close'].shift(window).iloc[-1]

# Price Forecast Box plots
fig = go.Figure()
fig.update_layout(template='plotly_dark',
                   title='Multi-timeframe %sD Close Forecast' % window)
for data_line,L in zip(pForecast,dLabels):
  fig.add_trace(go.Box(x=data_line,
                       name=L,
                       boxmean=True,
                       boxpoints='outliers'))
# Add last daily closing price
fig.add_vline(x=crypto['close'].iloc[-2],
              annotation_text='%.2fk' % (crypto['close'].iloc[-2]/1000),
              annotation_position='top')
fig.show()

/usr/local/lib/python3.10/dist-packages/scipy/stats/_continuous_distns.py:6816: RuntimeWarning:

overflow encountered in exp

/usr/local/lib/python3.10/dist-packages/scipy/stats/_continuous_distns.py:6822: RuntimeWarning:

invalid value encountered in multiply

/usr/local/lib/python3.10/dist-packages/scipy/stats/_continuous_distns.py:6819: RuntimeWarning:

overflow encountered in multiply

/usr/local/lib/python3.10/dist-packages/scipy/stats/_continuous_distns.py:6821: RuntimeWarning:

overflow encountered in multiply



In [146]:
# Create Figure
fig = go.Figure()
fig.update_layout(template='plotly_dark',title ='Log Returns Z-Score')
# Add Asset Return Volatility
fig.add_trace(go.Scatter(
    x=crypto['Date'],y=crypto['ret'],
    mode='markers',
    marker=dict(color=ret, size=3.5,
                colorscale='Portland'),
    name='Z-Score')
)
fig.show()

## Correlation

In [149]:
t_unit = [7,14,30,91]
df = pd.DataFrame()
df['close'] = crypto['close']
# Calculate SMAs
for i in t_unit:
  sma_name = 'SMA%s' % i
  df[sma_name] = df['close'].rolling(window=i,min_periods=1).mean()
# Calculate correlation of price and SMAs
corr = df['close'].rolling(window=30,min_periods=1).corr(df.iloc[:,1:])

# Add correlation figure
fig = make_subplots(rows=2, cols=1,
                    shared_xaxes=True)
fig.add_trace(go.Scatter(x=crypto['Date'],y=df['close'],marker_color='white',name='Price'),
              row=1,col=1)
for i in np.arange(1,5):
  fig.add_trace(go.Scatter(x=crypto['Date'],y=df.iloc[:,i],name=df.columns[i]),
              row=1,col=1)
fig.add_trace(go.Heatmap(
                    x=crypto['Date'],
                    y=df.iloc[:,1:].columns.values.tolist(),
                    z=corr.transpose(),
                    colorscale='RdBu_r'),
              row=2,col=1)
fig.update_layout(template='plotly_dark',height=900,legend=dict(orientation='h'),
                  hovermode ='x', title='30D Window Correlation',
                  yaxis=dict(domain=[0.22,1]),yaxis2=dict(domain=[0,0.2]))
fig.update_yaxes(type='log',row=1,col=1)
fig.show()

## Risk factor (not reliable, still working on it)

In [148]:
# Detrend Extension of Price from Non-Bubble Regression Curve
crypto['Detrend'] = np.log10(crypto['close']/crypto['NB'])
# Fit f(x) = a*(x+b) + c to Detrended extension
detrendDateFilter = pDates.iloc[-2]
xData = crypto.idx[crypto['Date'] < detrendDateFilter]
yData = crypto.Detrend[crypto['Date'] < detrendDateFilter]
popt, pcov = opt.curve_fit(linearEq, xData, yData)
f0 = popt[0]*(0+popt[1]) + popt[2]
risk = f0*crypto['Detrend']/linearEq(crypto.idx,*popt)
crypto['Risk'] = (risk - min(risk)) / (max(risk) - min(risk))

# Plot Risk
# Create figure with secondary y-axis
fig3 = make_subplots(specs=[[{"secondary_y": True}]])
fig3.update_yaxes(type="log")
fig3.update_layout(template='plotly_dark', showlegend=True, height=800,
                   legend=dict(orientation='h'),
                   yaxis=dict(type='linear'))

# Add traces
fig3.add_trace(
    go.Scatter(x=crypto['Date'], y=crypto['Risk'],
               name="Risk Factor", marker=dict(color='rgb(255,255,255)')),
    secondary_y=False
)

fig3.add_trace(
    go.Scatter(x=crypto['Date'], y=crypto['close'],
               name="Price (USD)",marker=dict(color='yellow')),
    secondary_y=True
)

# Set y-axes titles
fig3.update_yaxes(title_text="Risk Factor", secondary_y=False)
fig3.update_yaxes(title_text="Price (USD)", secondary_y=True, showgrid=False)

fig3.show()